# Set up imports

In [27]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# less than 10 documents,
id2word = corpora.Dictionary(data)
id2word.filter_extremes(no_below = 4)

In [11]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [12]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [13]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [14]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=5, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [15]:
ldaseq.print_topics(time=0) # at timeslice 1, those are the topics

[[('model', 0.02531369028174191),
  ('network', 0.011725380390179027),
  ('neural', 0.009473846187017338),
  ('system', 0.006939434679791044),
  ('neuron', 0.006751871460139705),
  ('human', 0.006169985606125803),
  ('show', 0.006026656415413322),
  ('data', 0.005688687436132614),
  ('stimulus', 0.005365312598487021),
  ('learning', 0.005198806788815757),
  ('time', 0.005069733709403875),
  ('dynamic', 0.005026589128040813),
  ('input', 0.005003788908455039),
  ('using', 0.004999811018890155),
  ('information', 0.0049839423573790195),
  ('activity', 0.004909254470657756),
  ('response', 0.004600731837725506),
  ('spike', 0.004305498395924818),
  ('brain', 0.004301325104135065),
  ('based', 0.003990259397754154)],
 [('model', 0.03352217208894737),
  ('distribution', 0.017900889309290968),
  ('data', 0.015667071187052035),
  ('inference', 0.01398675346668105),
  ('method', 0.012977336298932378),
  ('process', 0.010421571982908249),
  ('approach', 0.009364404804724148),
  ('bayesian', 0.0

In [16]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('model', 0.02531369028174191),
  ('network', 0.011725380390179027),
  ('neural', 0.009473846187017338),
  ('system', 0.006939434679791044),
  ('neuron', 0.006751871460139705),
  ('human', 0.006169985606125803),
  ('show', 0.006026656415413322),
  ('data', 0.005688687436132614),
  ('stimulus', 0.005365312598487021),
  ('learning', 0.005198806788815757),
  ('time', 0.005069733709403875),
  ('dynamic', 0.005026589128040813),
  ('input', 0.005003788908455039),
  ('using', 0.004999811018890155),
  ('information', 0.0049839423573790195),
  ('activity', 0.004909254470657756),
  ('response', 0.004600731837725506),
  ('spike', 0.004305498395924818),
  ('brain', 0.004301325104135065),
  ('based', 0.003990259397754154)],
 [('model', 0.025347753879669036),
  ('network', 0.011602349071197187),
  ('neural', 0.009358609598417353),
  ('system', 0.006911341595983824),
  ('neuron', 0.0067890546133173866),
  ('human', 0.006201803106046609),
  ('show', 0.0060568951136604635),
  ('data', 0.0057163025474

In [17]:
ldaseq.print_topic_times(topic=1)

[[('model', 0.03352217208894737),
  ('distribution', 0.017900889309290968),
  ('data', 0.015667071187052035),
  ('inference', 0.01398675346668105),
  ('method', 0.012977336298932378),
  ('process', 0.010421571982908249),
  ('approach', 0.009364404804724148),
  ('bayesian', 0.00927764960313411),
  ('variable', 0.00868444101657492),
  ('algorithm', 0.0071458197224181525),
  ('structure', 0.007080749427620896),
  ('parameter', 0.0066160252118129485),
  ('gaussian', 0.006576679676045749),
  ('using', 0.006244402378528726),
  ('prior', 0.006179143111277025),
  ('probabilistic', 0.005937404070714055),
  ('latent', 0.00589928492931607),
  ('based', 0.005831552034179328),
  ('show', 0.0057786351456204765),
  ('sample', 0.0053272301003441744)],
 [('model', 0.033630888115932),
  ('distribution', 0.017946391216707283),
  ('data', 0.01570430687739721),
  ('inference', 0.014018818923223876),
  ('method', 0.013006279881839453),
  ('process', 0.010442733064530833),
  ('approach', 0.009381814215432502

In [18]:
ldaseq.print_topic_times(topic=2)

[[('algorithm', 0.024830271160851982),
  ('problem', 0.01864801778159272),
  ('method', 0.016863998492154437),
  ('function', 0.010365398362874532),
  ('data', 0.0101791480194839),
  ('kernel', 0.009794137718642643),
  ('matrix', 0.009574371090352128),
  ('learning', 0.008130246735286718),
  ('sparse', 0.00806341106439745),
  ('show', 0.00788659469510595),
  ('linear', 0.007040073076537377),
  ('result', 0.006453227753802103),
  ('optimization', 0.006316361338583592),
  ('paper', 0.006257928051824081),
  ('analysis', 0.005802699719637356),
  ('regression', 0.005798506822235693),
  ('convex', 0.005657001083015234),
  ('clustering', 0.005531837147558118),
  ('gradient', 0.005329526324856568),
  ('convergence', 0.004942350360128746)],
 [('algorithm', 0.02477889876805405),
  ('problem', 0.01870895248305989),
  ('method', 0.01691658206095748),
  ('function', 0.010390858923469581),
  ('data', 0.01020544671571618),
  ('kernel', 0.00981824706147507),
  ('matrix', 0.009597795612168015),
  ('lea

In [19]:
ldaseq.print_topic_times(topic=3)

[[('algorithm', 0.03072073491310389),
  ('learning', 0.020077767985046915),
  ('problem', 0.01588866559204276),
  ('bound', 0.012011554787915995),
  ('function', 0.010445526974547674),
  ('show', 0.009179516977916285),
  ('policy', 0.007169115537985273),
  ('result', 0.00689998988361478),
  ('loss', 0.006306330447227478),
  ('online', 0.006068724090871945),
  ('optimal', 0.005707420944219543),
  ('paper', 0.005025232032247912),
  ('decision', 0.004989724644615885),
  ('time', 0.004939710447143288),
  ('new', 0.004861723757432975),
  ('setting', 0.0047516003978081665),
  ('case', 0.004653831311939006),
  ('also', 0.004639548269408284),
  ('approach', 0.00463497437552546),
  ('regret', 0.004533665386022596)],
 [('algorithm', 0.030824925153092125),
  ('learning', 0.02013616076253647),
  ('problem', 0.015929993425499892),
  ('bound', 0.012041922508696843),
  ('function', 0.010470175251992876),
  ('show', 0.009199267991406647),
  ('policy', 0.007183198279431108),
  ('result', 0.006913306376

In [20]:
ldaseq.print_topic_times(topic=4)

[[('image', 0.0183040415300994),
  ('learning', 0.017188974808783442),
  ('data', 0.015158143604679762),
  ('feature', 0.01510971666316011),
  ('model', 0.013711120327174243),
  ('method', 0.012800192308838509),
  ('task', 0.010678840425782017),
  ('object', 0.009934034644919095),
  ('approach', 0.00937317046293919),
  ('training', 0.006976051395438457),
  ('classification', 0.006936115572013072),
  ('set', 0.006848522020028508),
  ('problem', 0.0065067428037831046),
  ('show', 0.006060889513587065),
  ('using', 0.005616791828095437),
  ('performance', 0.005023529113448369),
  ('representation', 0.004900779599748655),
  ('result', 0.0048879407148374665),
  ('paper', 0.0047697274265329345),
  ('propose', 0.004717218226473043)],
 [('image', 0.01813061355861053),
  ('learning', 0.017249408163881732),
  ('data', 0.01522772940792429),
  ('feature', 0.015178893494552474),
  ('model', 0.013755376809074241),
  ('method', 0.01285277947810301),
  ('task', 0.010718810756821089),
  ('object', 0.00

In [21]:
# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[5.97210430e-01 4.02165220e-01 2.08116545e-04 2.08116545e-04
 2.08116545e-04]


In [22]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [23]:
ldaseq.print_topic_times(1) # evolution of values for first time slice


[[('model', 0.03352217208894737),
  ('distribution', 0.017900889309290968),
  ('data', 0.015667071187052035),
  ('inference', 0.01398675346668105),
  ('method', 0.012977336298932378),
  ('process', 0.010421571982908249),
  ('approach', 0.009364404804724148),
  ('bayesian', 0.00927764960313411),
  ('variable', 0.00868444101657492),
  ('algorithm', 0.0071458197224181525),
  ('structure', 0.007080749427620896),
  ('parameter', 0.0066160252118129485),
  ('gaussian', 0.006576679676045749),
  ('using', 0.006244402378528726),
  ('prior', 0.006179143111277025),
  ('probabilistic', 0.005937404070714055),
  ('latent', 0.00589928492931607),
  ('based', 0.005831552034179328),
  ('show', 0.0057786351456204765),
  ('sample', 0.0053272301003441744)],
 [('model', 0.033630888115932),
  ('distribution', 0.017946391216707283),
  ('data', 0.01570430687739721),
  ('inference', 0.014018818923223876),
  ('method', 0.013006279881839453),
  ('process', 0.010442733064530833),
  ('approach', 0.009381814215432502

In [24]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.675778532797036
CV1 0.38848694932686734
U_Mass2 -1.675778532797036
CV2 0.38848694932686734
U_Mass3 -1.681480522768675
CV3 0.3884869493268674
U_Mass4 -1.6982866988613914
CV4 0.3935796287078176
U_Mass5 -1.7098577219835094
CV5 0.3938117915120232
U_Mass6 -1.7105071377533405
CV6 0.3938117915120232
U_Mass7 -1.6827842798496317
CV7 0.40085271568075037
U_Mass8 -1.704899819526916
CV8 0.4039015061253292
U_Mass9 -1.7102354820026975
CV9 0.40636957145343444
U_Mass10 -1.7105738360023814
CV10 0.40906307177912044
U_Mass11 -1.715149825539773
CV11 0.3952107949414013
U_Mass12 -1.7248791004994384
CV12 0.4081807904384106


In [25]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/